In [1]:
from random import random
from numpy import load
from numpy import zeros
from numpy import ones
from numpy import asarray
from numpy.random import randint
from keras.optimizers import Adam
from keras.initializers import RandomNormal
from keras.models import Model
from keras.models import Input
from keras.layers import Conv2D
from keras.layers import Conv2DTranspose
from keras.layers import LeakyReLU
from keras.layers import Activation
from keras.layers import Concatenate
from keras_contrib.layers.normalization.instancenormalization import InstanceNormalization
from matplotlib import pyplot

Using TensorFlow backend.


In [2]:
# define the discriminator model
def define_discriminator(image_shape):
    # weight initialization
    init = RandomNormal(stddev=0.02)
    # source image input
    in_image = Input(shape=image_shape)
    # C64
    d = Conv2D(64, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(in_image)
    d = LeakyReLU(alpha=0.2)(d)
    # C128
    d = Conv2D(128, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
    d = InstanceNormalization(axis=-1)(d)
    d = LeakyReLU(alpha=0.2)(d)
    # C256
    d = Conv2D(256, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
    d = InstanceNormalization(axis=-1)(d)
    d = LeakyReLU(alpha=0.2)(d)
    # C512
    d = Conv2D(512, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
    d = InstanceNormalization(axis=-1)(d)
    d = LeakyReLU(alpha=0.2)(d)
    # second last output layer
    d = Conv2D(512, (4,4), padding='same', kernel_initializer=init)(d)
    d = InstanceNormalization(axis=-1)(d)
    d = LeakyReLU(alpha=0.2)(d)
    # patch output
    patch_out = Conv2D(1, (4,4), padding='same', kernel_initializer=init)(d)
    # define model
    model = Model(in_image, patch_out)
    # compile model
    model.compile(loss='mse', optimizer=Adam(lr=0.0002, beta_1=0.5), loss_weights=[0.5])
    return model

# generator a resnet block
def resnet_block(n_filters, input_layer):
    # weight initialization
    init = RandomNormal(stddev=0.02)
    # first layer convolutional layer
    g = Conv2D(n_filters, (3,3), padding='same', kernel_initializer=init)(input_layer)
    g = InstanceNormalization(axis=-1)(g)
    g = Activation('relu')(g)
    # second convolutional layer
    g = Conv2D(n_filters, (3,3), padding='same', kernel_initializer=init)(g)
    g = InstanceNormalization(axis=-1)(g)
    # concatenate merge channel-wise with input layer
    g = Concatenate()([g, input_layer])
    return g

# define the standalone generator model
def define_generator(image_shape, n_resnet=6):
    # weight initialization
    init = RandomNormal(stddev=0.02)
    # image input
    in_image = Input(shape=image_shape)
    # c7s1-64
    g = Conv2D(64, (7,7), padding='same', kernel_initializer=init)(in_image)
    g = InstanceNormalization(axis=-1)(g)
    g = Activation('relu')(g)
    # d128
    g = Conv2D(128, (3,3), strides=(2,2), padding='same', kernel_initializer=init)(g)
    g = InstanceNormalization(axis=-1)(g)
    g = Activation('relu')(g)
    # d256
    g = Conv2D(256, (3,3), strides=(2,2), padding='same', kernel_initializer=init)(g)
    g = InstanceNormalization(axis=-1)(g)
    g = Activation('relu')(g)
    # R256
    for _ in range(n_resnet):
        g = resnet_block(256, g)
    # u128
    g = Conv2DTranspose(128, (3,3), strides=(2,2), padding='same', kernel_initializer=init)(g)
    g = InstanceNormalization(axis=-1)(g)
    g = Activation('relu')(g)
    # u64
    g = Conv2DTranspose(64, (3,3), strides=(2,2), padding='same', kernel_initializer=init)(g)
    g = InstanceNormalization(axis=-1)(g)
    g = Activation('relu')(g)
    # c7s1-3
    g = Conv2D(3, (7,7), padding='same', kernel_initializer=init)(g)
    g = InstanceNormalization(axis=-1)(g)
    out_image = Activation('tanh')(g)
    # define model
    model = Model(in_image, out_image)
    return model

# define a composite model for updating generators by adversarial and cycle loss
def define_composite_model(g_model_1, d_model, g_model_2, image_shape):
    # ensure the model we're updating is trainable
    g_model_1.trainable = True
    # mark discriminator as not trainable
    d_model.trainable = False
    # mark other generator model as not trainable
    g_model_2.trainable = False
    # discriminator element
    input_gen = Input(shape=image_shape)
    gen1_out = g_model_1(input_gen)
    output_d = d_model(gen1_out)
    # identity element
    input_id = Input(shape=image_shape)
    output_id = g_model_1(input_id)
    # forward cycle
    output_f = g_model_2(gen1_out)
    # backward cycle
    gen2_out = g_model_2(input_id)
    output_b = g_model_1(gen2_out)
    # define model graph
    model = Model([input_gen, input_id], [output_d, output_id, output_f, output_b])
    # define optimization algorithm configuration
    opt = Adam(lr=0.0002, beta_1=0.5)
    # compile model with weighting of least squares loss and L1 loss
    model.compile(loss=['mse', 'mae', 'mae', 'mae'], loss_weights=[1, 5, 10, 10], optimizer=opt)
    return model

In [3]:
# load and prepare training images
def load_real_samples(filename):
    # load the dataset
    data = load(filename)
    # unpack arrays
    X1, X2 = data['arr_0'], data['arr_1']
    # scale from [0,255] to [-1,1]
    X1 = (X1 - 127.5) / 127.5
    X2 = (X2 - 127.5) / 127.5
    return [X1, X2]

# select a batch of random samples, returns images and target
def generate_real_samples(dataset, n_samples, patch_shape):
    # choose random instances
    ix = randint(0, dataset.shape[0], n_samples)
    # retrieve selected images
    X = dataset[ix]
    # generate 'real' class labels (1)
    y = ones((n_samples, patch_shape, patch_shape, 1))
    return X, y

# generate a batch of images, returns images and targets
def generate_fake_samples(g_model, dataset, patch_shape):
    # generate fake instance
    X = g_model.predict(dataset)
    # create 'fake' class labels (0)
    y = zeros((len(X), patch_shape, patch_shape, 1))
    return X, y

# save the generator models to file
def save_models(step, g_model_AtoB, g_model_BtoA):
    # save the first generator model
    filename1 = 'g_model_AtoB_%06d.h5' % (step+1)
    g_model_AtoB.save(filename1)
    # save the second generator model
    filename2 = 'g_model_BtoA_%06d.h5' % (step+1)
    g_model_BtoA.save(filename2)
    print('>Saved: %s and %s' % (filename1, filename2))

# generate samples and save as a plot and save the model
def summarize_performance(step, g_model, trainX, name, n_samples=5):
    # select a sample of input images
    X_in, _ = generate_real_samples(trainX, n_samples, 0)
    # generate translated images
    X_out, _ = generate_fake_samples(g_model, X_in, 0)
    # scale all pixels from [-1,1] to [0,1]
    X_in = (X_in + 1) / 2.0
    X_out = (X_out + 1) / 2.0
    # plot real images
    for i in range(n_samples):
        pyplot.subplot(2, n_samples, 1 + i)
        pyplot.axis('off')
        pyplot.imshow(X_in[i])
    # plot translated image
    for i in range(n_samples):
        pyplot.subplot(2, n_samples, 1 + n_samples + i)
        pyplot.axis('off')
        pyplot.imshow(X_out[i])
    # save plot to file
    filename1 = '%s_generated_plot_%06d.png' % (name, (step+1))
    pyplot.savefig(filename1)
    pyplot.close()

# update image pool for fake images
def update_image_pool(pool, images, max_size=50):
    selected = list()
    for image in images:
        if len(pool) < max_size:
            # stock the pool
            pool.append(image)
            selected.append(image)
        elif random() < 0.5:
            # use image, but don't add it to the pool
            selected.append(image)
        else:
            # replace an existing image and use replaced image
            ix = randint(0, len(pool))
            selected.append(pool[ix])
            pool[ix] = image
    return asarray(selected)

# train cyclegan models
def train(d_model_A, d_model_B, g_model_AtoB, g_model_BtoA, c_model_AtoB, c_model_BtoA, dataset):
    # define properties of the training run
    n_epochs, n_batch, = 100, 1
    # determine the output square shape of the discriminator
    n_patch = d_model_A.output_shape[1]
    # unpack dataset
    trainA, trainB = dataset
    # prepare image pool for fakes
    poolA, poolB = list(), list()
    # calculate the number of batches per training epoch
    bat_per_epo = int(len(trainA) / n_batch)
    # calculate the number of training iterations
    n_steps = bat_per_epo * n_epochs
    # manually enumerate epochs
    for i in range(n_steps):
        # select a batch of real samples
        X_realA, y_realA = generate_real_samples(trainA, n_batch, n_patch)
        X_realB, y_realB = generate_real_samples(trainB, n_batch, n_patch)
        # generate a batch of fake samples
        X_fakeA, y_fakeA = generate_fake_samples(g_model_BtoA, X_realB, n_patch)
        X_fakeB, y_fakeB = generate_fake_samples(g_model_AtoB, X_realA, n_patch)
        # update fakes from pool
        X_fakeA = update_image_pool(poolA, X_fakeA)
        X_fakeB = update_image_pool(poolB, X_fakeB)
        # update generator B->A via adversarial and cycle loss
        g_loss2, _, _, _, _  = c_model_BtoA.train_on_batch([X_realB, X_realA], [y_realA, X_realA, X_realB, X_realA])
        # update discriminator for A -> [real/fake]
        dA_loss1 = d_model_A.train_on_batch(X_realA, y_realA)
        dA_loss2 = d_model_A.train_on_batch(X_fakeA, y_fakeA)
        # update generator A->B via adversarial and cycle loss
        g_loss1, _, _, _, _ = c_model_AtoB.train_on_batch([X_realA, X_realB], [y_realB, X_realB, X_realA, X_realB])
        # update discriminator for B -> [real/fake]
        dB_loss1 = d_model_B.train_on_batch(X_realB, y_realB)
        dB_loss2 = d_model_B.train_on_batch(X_fakeB, y_fakeB)
        # summarize performance
        print('>%d, dA[%.3f,%.3f] dB[%.3f,%.3f] g[%.3f,%.3f]' % (i+1, dA_loss1,dA_loss2, dB_loss1,dB_loss2, g_loss1,g_loss2))
        # evaluate the model performance every so often
        if (i+1) % (bat_per_epo * 1) == 0:
            # plot A->B translation
            summarize_performance(i, g_model_AtoB, trainA, 'AtoB')
            # plot B->A translation
            summarize_performance(i, g_model_BtoA, trainB, 'BtoA')
        if (i+1) % (bat_per_epo * 5) == 0:
            # save the models
            save_models(i, g_model_AtoB, g_model_BtoA)

In [ ]:
# load image data
dataset = load_real_samples('Old2Young_64.npz')
print('Loaded', dataset[0].shape, dataset[1].shape)
# define input shape based on the loaded dataset
image_shape = dataset[0].shape[1:]
# generator: A -> B
g_model_AtoB = define_generator(image_shape)
# generator: B -> A
g_model_BtoA = define_generator(image_shape)
# discriminator: A -> [real/fake]
d_model_A = define_discriminator(image_shape)
# discriminator: B -> [real/fake]
d_model_B = define_discriminator(image_shape)
# composite: A -> B -> [real/fake, A]
c_model_AtoB = define_composite_model(g_model_AtoB, d_model_B, g_model_BtoA, image_shape)
# composite: B -> A -> [real/fake, B]
c_model_BtoA = define_composite_model(g_model_BtoA, d_model_A, g_model_AtoB, image_shape)
# train models
train(d_model_A, d_model_B, g_model_AtoB, g_model_BtoA, c_model_AtoB, c_model_BtoA, dataset)

Loaded (1522, 64, 64, 3) (7324, 64, 64, 3)
Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Use tf.cast instead.


C:\Users\sree-LM\Anaconda3\envs\t-gpu\lib\site-packages\keras\engine\training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


>1, dA[0.584,0.616] dB[1.193,0.780] g[17.243,16.585]
>2, dA[0.913,0.730] dB[0.709,0.474] g[17.623,17.704]
>3, dA[1.029,0.734] dB[1.367,0.499] g[16.763,17.758]
>4, dA[1.242,0.815] dB[0.935,1.234] g[19.398,17.361]
>5, dA[1.891,1.661] dB[1.526,1.018] g[17.940,18.828]
>6, dA[0.984,1.354] dB[1.349,1.808] g[22.356,20.151]
>7, dA[1.938,1.980] dB[3.069,1.387] g[16.993,20.322]
>8, dA[0.569,1.941] dB[4.000,1.376] g[19.173,18.435]
>9, dA[1.980,3.000] dB[5.804,0.557] g[18.077,20.434]
>10, dA[3.852,1.215] dB[3.217,0.802] g[18.008,18.091]
>11, dA[1.356,1.826] dB[1.724,1.334] g[15.512,18.244]
>12, dA[0.905,0.622] dB[0.622,0.606] g[17.065,17.490]
>13, dA[1.132,0.563] dB[1.702,1.122] g[18.728,18.022]
>14, dA[0.854,1.877] dB[3.730,1.882] g[18.739,18.837]
>15, dA[1.935,1.706] dB[1.477,0.697] g[17.993,19.628]
>16, dA[1.286,3.331] dB[2.199,0.684] g[16.646,23.081]
>17, dA[1.764,6.146] dB[2.783,0.551] g[17.500,22.145]
>18, dA[2.219,1.282] dB[2.959,0.468] g[16.185,16.393]
>19, dA[0.956,1.501] dB[1.768,0.549] 

>155, dA[0.053,0.200] dB[0.135,0.180] g[9.047,9.274]
>156, dA[0.212,0.125] dB[0.156,0.081] g[8.941,8.600]
>157, dA[0.084,0.057] dB[0.060,0.134] g[9.760,9.163]
>158, dA[0.055,0.017] dB[0.165,0.103] g[7.402,7.426]
>159, dA[0.055,1.052] dB[0.020,0.124] g[6.442,6.508]
>160, dA[0.114,0.205] dB[0.065,0.281] g[5.996,6.137]
>161, dA[0.341,0.060] dB[0.067,0.249] g[7.445,8.203]
>162, dA[0.084,0.282] dB[0.094,0.075] g[6.890,6.861]
>163, dA[0.103,0.115] dB[0.084,0.203] g[8.926,7.809]
>164, dA[0.067,0.113] dB[0.130,0.356] g[6.424,7.152]
>165, dA[0.090,0.159] dB[0.099,0.598] g[8.906,8.999]
>166, dA[0.151,0.051] dB[0.113,0.809] g[7.123,7.071]
>167, dA[0.057,0.052] dB[0.114,0.222] g[11.124,9.862]
>168, dA[0.231,0.220] dB[0.074,0.134] g[8.754,8.388]
>169, dA[0.114,0.201] dB[0.137,0.284] g[6.173,5.923]
>170, dA[0.165,0.137] dB[0.136,0.132] g[8.349,8.540]
>171, dA[0.172,0.105] dB[0.146,0.047] g[7.298,6.453]
>172, dA[0.135,0.253] dB[0.028,0.166] g[8.728,9.352]
>173, dA[0.166,0.085] dB[0.067,0.263] g[8.036

>310, dA[0.091,0.133] dB[0.035,0.279] g[7.864,8.361]
>311, dA[0.048,0.062] dB[0.211,0.025] g[7.322,7.072]
>312, dA[0.235,0.095] dB[0.064,0.011] g[8.491,8.023]
>313, dA[0.093,0.239] dB[0.069,0.117] g[6.086,6.428]
>314, dA[0.255,0.058] dB[0.055,0.018] g[6.815,6.848]
>315, dA[0.031,0.188] dB[0.270,0.541] g[8.927,10.696]
>316, dA[0.057,0.062] dB[0.036,0.057] g[11.137,10.623]
>317, dA[0.026,0.194] dB[0.024,0.037] g[7.122,8.174]
>318, dA[0.195,0.116] dB[0.041,0.203] g[8.853,8.014]
>319, dA[0.135,0.063] dB[0.095,0.195] g[9.364,10.207]
>320, dA[0.052,0.049] dB[0.152,0.122] g[6.322,6.545]
>321, dA[0.200,0.491] dB[0.053,0.188] g[10.051,10.662]
>322, dA[0.071,0.084] dB[0.034,0.264] g[7.364,7.434]
>323, dA[0.334,0.092] dB[0.193,0.218] g[5.622,6.809]
>324, dA[0.095,0.065] dB[0.093,0.545] g[6.630,7.128]
>325, dA[0.078,0.516] dB[0.073,0.096] g[7.884,7.922]
>326, dA[0.088,0.133] dB[0.327,0.056] g[8.235,8.014]
>327, dA[0.124,0.194] dB[0.158,0.692] g[5.846,6.749]
>328, dA[0.076,0.194] dB[0.068,0.213] g[

...

>108414, dA[0.000,0.000] dB[0.001,0.027] g[2.473,2.691]
>108415, dA[0.000,0.000] dB[0.135,0.002] g[3.017,4.241]
>108416, dA[0.000,0.000] dB[0.003,0.036] g[2.616,3.299]
>108417, dA[0.000,0.000] dB[0.048,0.001] g[1.987,2.479]
>108418, dA[0.000,0.000] dB[0.004,0.004] g[3.667,3.602]
>108419, dA[0.000,0.000] dB[0.006,0.273] g[1.845,3.109]
>108420, dA[0.000,0.000] dB[0.060,0.005] g[3.111,3.124]
>108421, dA[0.000,0.000] dB[0.025,0.001] g[2.801,2.894]
>108422, dA[0.000,0.000] dB[0.001,0.013] g[2.221,3.185]
>108423, dA[0.000,0.000] dB[0.013,0.003] g[2.378,2.723]
>108424, dA[0.000,0.000] dB[0.000,0.010] g[2.197,2.947]
>108425, dA[0.000,0.000] dB[0.001,0.004] g[4.706,4.322]
>108426, dA[0.000,0.000] dB[0.022,0.012] g[2.605,2.763]
>108427, dA[0.000,0.000] dB[0.002,0.008] g[1.888,2.512]
>108428, dA[0.000,0.000] dB[0.001,0.019] g[2.335,2.735]
>108429, dA[0.000,0.000] dB[0.035,0.003] g[2.820,2.687]
>108430, dA[0.000,0.000] dB[0.001,0.002] g[3.148,3.209]
>108431, dA[0.000,0.001] dB[0.003,0.005] g[3.350

>108561, dA[0.003,0.000] dB[0.006,0.001] g[3.070,2.551]
>108562, dA[0.000,0.000] dB[0.003,0.002] g[2.394,2.992]
>108563, dA[0.000,0.000] dB[0.001,0.002] g[3.019,3.168]
>108564, dA[0.000,0.000] dB[0.001,0.001] g[2.908,3.143]
>108565, dA[0.000,0.000] dB[0.006,0.009] g[2.871,3.325]
>108566, dA[0.000,0.000] dB[0.063,0.012] g[1.922,2.489]
>108567, dA[0.000,0.000] dB[0.003,0.005] g[2.428,2.767]
>108568, dA[0.000,0.000] dB[0.067,0.065] g[2.232,2.842]
>108569, dA[0.000,0.000] dB[0.002,0.005] g[3.420,3.843]
>108570, dA[0.000,0.000] dB[0.079,0.009] g[2.360,2.679]
>108571, dA[0.000,0.000] dB[0.020,0.003] g[2.880,3.036]
>108572, dA[0.000,0.000] dB[0.002,0.086] g[2.066,2.985]
>108573, dA[0.000,0.000] dB[0.001,0.003] g[3.252,3.335]
>108574, dA[0.000,0.000] dB[0.002,0.002] g[2.339,2.804]
>108575, dA[0.000,0.000] dB[0.003,0.019] g[2.204,2.845]
>108576, dA[0.000,0.000] dB[0.002,0.005] g[2.933,3.593]
>108577, dA[0.000,0.000] dB[0.001,0.018] g[3.727,3.625]
>108578, dA[0.000,0.000] dB[0.001,0.003] g[2.530

>108708, dA[0.000,0.000] dB[0.065,0.004] g[2.760,3.146]
>108709, dA[0.000,0.000] dB[0.347,0.195] g[1.896,2.929]
>108710, dA[0.000,0.000] dB[0.007,0.014] g[2.078,2.929]
>108711, dA[0.000,0.000] dB[0.089,0.004] g[2.153,2.766]
>108712, dA[0.000,0.000] dB[0.006,0.001] g[2.046,2.939]
>108713, dA[0.000,0.000] dB[0.010,0.090] g[1.652,2.285]
>108714, dA[0.000,0.000] dB[0.015,0.066] g[1.607,2.425]
>108715, dA[0.000,0.000] dB[0.046,0.005] g[2.547,2.844]
>108716, dA[0.000,0.000] dB[0.002,0.017] g[3.587,3.324]
>108717, dA[0.000,0.000] dB[0.009,0.002] g[2.052,2.455]
>108718, dA[0.000,0.000] dB[0.004,0.012] g[2.268,2.751]
>108719, dA[0.000,0.000] dB[0.060,0.017] g[2.263,2.475]
>108720, dA[0.000,0.000] dB[0.002,0.002] g[2.965,3.454]
>108721, dA[0.000,0.000] dB[0.001,0.047] g[2.020,2.326]
>108722, dA[0.000,0.000] dB[0.001,0.011] g[2.735,2.803]
>108723, dA[0.000,0.000] dB[0.015,0.005] g[2.293,2.510]
>108724, dA[0.000,0.000] dB[0.024,0.002] g[2.488,2.722]
>108725, dA[0.000,0.000] dB[0.004,0.113] g[1.699

>108855, dA[0.000,0.000] dB[0.023,0.010] g[2.452,2.907]
>108856, dA[0.000,0.000] dB[0.005,0.052] g[2.469,3.043]
>108857, dA[0.000,0.000] dB[0.225,0.006] g[2.391,2.687]
>108858, dA[0.000,0.000] dB[0.002,0.003] g[2.429,2.970]
>108859, dA[0.000,0.000] dB[0.000,0.024] g[2.343,3.246]
>108860, dA[0.000,0.000] dB[0.001,0.008] g[2.313,2.897]
>108861, dA[0.000,0.000] dB[0.002,0.002] g[2.592,2.956]
>108862, dA[0.000,0.000] dB[0.237,0.004] g[2.510,2.818]
>108863, dA[0.000,0.000] dB[0.005,0.035] g[2.002,2.504]
>108864, dA[0.000,0.000] dB[0.002,0.116] g[2.425,2.850]
>108865, dA[0.000,0.000] dB[0.004,0.022] g[2.440,3.193]
>108866, dA[0.000,0.000] dB[0.003,0.002] g[3.186,2.628]
>108867, dA[0.000,0.000] dB[0.012,0.001] g[3.013,3.025]
>108868, dA[0.000,0.000] dB[0.017,0.067] g[2.117,2.831]
>108869, dA[0.000,0.000] dB[0.088,0.002] g[2.616,2.455]
>108870, dA[0.000,0.000] dB[0.003,0.001] g[2.943,3.517]
>108871, dA[0.000,0.000] dB[0.002,0.003] g[2.727,3.072]
>108872, dA[0.000,0.000] dB[0.003,0.001] g[2.244

>109002, dA[0.000,0.000] dB[0.030,0.006] g[2.607,2.835]
>109003, dA[0.000,0.000] dB[0.003,0.015] g[2.500,3.135]
>109004, dA[0.000,0.000] dB[0.005,0.003] g[2.565,3.011]
>109005, dA[0.000,0.000] dB[0.011,0.002] g[3.067,2.898]
>109006, dA[0.000,0.000] dB[0.002,0.001] g[3.371,3.044]
>109007, dA[0.000,0.000] dB[0.003,0.001] g[2.387,2.478]
>109008, dA[0.000,0.000] dB[0.001,0.005] g[3.047,3.147]
>109009, dA[0.000,0.000] dB[0.001,0.002] g[2.607,3.033]
>109010, dA[0.000,0.000] dB[0.005,0.005] g[2.757,2.790]
>109011, dA[0.000,0.000] dB[0.075,0.001] g[2.324,2.668]
>109012, dA[0.000,0.000] dB[0.002,0.011] g[2.531,3.243]
>109013, dA[0.000,0.000] dB[0.000,0.075] g[3.084,3.631]
>109014, dA[0.000,0.000] dB[0.006,0.004] g[2.290,3.017]
>109015, dA[0.000,0.000] dB[0.005,0.001] g[2.784,2.931]
>109016, dA[0.000,0.000] dB[0.029,0.000] g[2.914,3.179]
>109017, dA[0.000,0.000] dB[0.000,0.009] g[3.832,3.856]
>109018, dA[0.000,0.000] dB[0.029,0.001] g[2.625,2.832]
>109019, dA[0.000,0.000] dB[0.003,0.026] g[2.346